# Install Car Dealership Stored Procedures

In [ ]:
from data201 import db_connection

In [ ]:
conn = db_connection(config_file = 'CarDealership.ini')
cursor = conn.cursor()

### **1.a** What sales did each salesperson make during a given month?

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS sales_of_month')

cursor.execute( 
    """
    CREATE PROCEDURE sales_of_month(IN month INT)
    BEGIN
        SELECT sp.name AS spname, 
               car.company, car.model, 
               c.name AS cname, c.gender AS cgender, car.price
        FROM salesperson sp
        JOIN transaction t
          ON t.salesperson_id = sp.id
        JOIN car
          ON car.transaction_id = t.id
        JOIN customer c
          ON c.id = t.customer_id
        WHERE t.month = month
        ORDER BY spname, car.company, car.model, cgender;
    END
    """
)

### **1.b** How many sales did each salesperson make during a given month?

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS sales_counts_of_month')

cursor.execute( 
    """
    CREATE PROCEDURE sales_counts_of_month(IN month INT)
    BEGIN
        SELECT sp.name AS spname, COUNT(sp.name) AS cars_sold
        FROM salesperson sp
        JOIN transaction t
          ON t.salesperson_id = sp.id
        JOIN car
          ON car.transaction_id = t.id
        JOIN customer c
          ON c.id = t.customer_id
        WHERE t.month = month
        GROUP BY spname
        ORDER BY spname;
    END
    """
)

### **1.c** What is the highest number of sales by a salesperson during a given month?
#### Return the number via the `OUT highest INT` parameter, whose value is set by the`SELECT INTO`. Therefore, this procedure does not return any rows.

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS highest_sales_of_month')

cursor.execute( 
    """
    CREATE PROCEDURE highest_sales_of_month(IN month INT, 
                                            OUT highest INT)
    BEGIN
        SELECT COUNT(sp.name) INTO highest
        FROM salesperson sp
        JOIN transaction t
          ON t.salesperson_id = sp.id
        WHERE t.month = month
        GROUP BY sp.name
        ORDER BY count(sp.name) DESC
        LIMIT 1;
    END
    """
)

### **1.c** Who are the salesperson(s) of a given month (those who make the highest sales)? 
#### During the all to procedure `highest_sales_of_month`, user-defined variable `@highest_sales` will receive the value of the procedure's `OUT` parameter. 

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS salespersons_of_the_month')

cursor.execute( 
    """
    CREATE PROCEDURE salespersons_of_the_month(IN month INT)
    BEGIN
        CALL highest_sales_of_month(month, @highest_sales);
    
        SELECT sp.name AS spname, COUNT(sp.name) AS cars_sold 
        FROM salesperson sp
        JOIN transaction t
          ON t.salesperson_id = sp.id
        WHERE t.month = month
        GROUP BY spname
        HAVING cars_sold = @highest_sales
        ORDER BY spname;
    END
    """
)

In [ ]:
cursor.close()
conn.close()